# Interactive Web Maps of COVID19 data in Python

## Libraries

For this session, we will be using two libraries: folium and altair. Make sure to install the libraries using `pip` or `conda`. If you have reached this Jupyter notebook via the IDRE GitHub page, or, if you installed Anaconda and ran `requirements.txt`, your library should already be installed. If not, uncomment the install code below and run them.


In [ ]:
# !conda install -c conda-forge folium

Some resources:
* official folium documentation: https://python-visualization.github.io/folium/index.html 
* https://coderzcolumn.com/tutorials/data-science/interactive-maps-choropleth-scattermap-using-folium
* a simple jupyter notebook with examples: https://nbviewer.jupyter.org/github/python-visualization/folium/blob/master/examples/Features.ipynb
* choropleth mapping: https://coderzcolumn.com/tutorials/data-science/interactive-maps-choropleth-scattermap-using-folium
* working with geopandas: http://andrewgaidus.com/leaflet_webmaps_python/

In [18]:
import folium

Create your first interactive map.
* `location` is an array of [latitute, longitude]
* `zoom_start` is the default zoom level, 0 being the entire planet, 16 being very zoomed in (block level)
* `control_scale` adds a scale to the map
* `height` controls the height of the map

In [19]:
# Create a Map instance
map = folium.Map(location=[34,-118], 
               zoom_start=8, 
               control_scale=True,
               height=400)
map

You can choose to display a different basemap using the `tiles` property:
* `OpenStreetMap`
* `Stamen` (Terrain, Toner, and Watercolor)
* `CartoDB` (positron and dark_matter)

In [20]:
# Create a Map instance with different basemap
map = folium.Map(location=[34,-118], 
               zoom_start=8, 
               control_scale=True,
               height=400,
               tiles='CartoDB dark_matter',
               attr= '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>')
map

## Vector layers

https://python-visualization.github.io/folium/modules.html#module-folium.vector_layers

In [21]:
# add a circle
folium.CircleMarker(
    radius=100,
    location=[34,-118],
    color='crimson',
    fill=False,
).add_to(map)
map

In [22]:
# reset the map (only way to get rid of circles)
map = folium.Map(location=[34,-118], 
                zoom_start=8, 
                control_scale=True,
                height=400,
                tiles='CartoDB dark_matter',
                attr= '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>')

In [23]:
# get latimes covid19 data
import pandas as pd

latimes = pd.read_csv(
    "https://raw.githubusercontent.com/datadesk/california-coronavirus-data/master/latimes-place-totals.csv"
)
latimes


date       county  fips            place  confirmed_cases note  \
0      2020-07-16      Alameda   1.0  Address Unknown               37  NaN   
1      2020-07-16      Alameda   1.0          Alameda              136  NaN   
2      2020-07-16      Alameda   1.0           Albany               23  NaN   
3      2020-07-16      Alameda   1.0         Berkeley              295  NaN   
4      2020-07-16      Alameda   1.0           Dublin               92  NaN   
...           ...          ...   ...              ...              ...  ...   
79716  2020-03-16  Los Angeles  37.0       West Adams                1  NaN   
79717  2020-03-16  Los Angeles  37.0       West Hills                3  NaN   
79718  2020-03-16  Los Angeles  37.0   West Hollywood                5  NaN   
79719  2020-03-16  Los Angeles  37.0      West Vernon                1  NaN   
79720  2020-03-16  Los Angeles  37.0      Westchester                1  NaN   

                x          y  
0             NaN        NaN  
1     -122.274444  37.756111  
2     -122.297778  37.886944  
3     -122.272778  37.871667  
4     -121.935833  37.702222  
...           ...        ...  
79716 -118.307847  34.035612  
79717 -118.636070  34.211472  
79718 -118.371765  34.088278  
79719 -118.300192  34.000114  
79720 -118.406070  33.952357  

[79721 rows x 8 columns]

In [24]:
# create a subset dataset for a single day in Los Angeles
latimes_today = latimes.query("date == '2020-07-14' & county == 'Los Angeles'")
latimes_today

date       county  fips            place  confirmed_cases note  \
1936  2020-07-14  Los Angeles  37.0            Acton               34  NaN   
1937  2020-07-14  Los Angeles  37.0  Adams-Normandie              131  NaN   
1938  2020-07-14  Los Angeles  37.0     Agoura Hills               78  NaN   
1939  2020-07-14  Los Angeles  37.0       Agua Dulce               15  NaN   
1940  2020-07-14  Los Angeles  37.0         Alhambra              640  NaN   
...          ...          ...   ...              ...              ...  ...   
2259  2020-07-14  Los Angeles  37.0       Wilmington              844  NaN   
2260  2020-07-14  Los Angeles  37.0  Wilshire Center              607  NaN   
2261  2020-07-14  Los Angeles  37.0         Winnetka              632  NaN   
2262  2020-07-14  Los Angeles  37.0         Wiseburn               60  NaN   
2263  2020-07-14  Los Angeles  37.0   Woodland Hills              426  NaN   

               x          y  
1936 -118.216138  34.481366  
1937 -118.302397  34.029122  
1938 -118.760876  34.151007  
1939 -118.323810  34.497963  
1940 -118.135504  34.083961  
...          ...        ...  
2259 -118.253276  33.785869  
2260 -118.295338  34.068376  
2261 -118.575929  34.213111  
2262 -118.365742  33.909520  
2263 -118.604522  34.166350  

[328 rows x 8 columns]

## Let's chart with altair
* altair documentation: https://altair-viz.github.io/getting_started/overview.html

In [25]:
import altair as alt

In [26]:
# reset the map (only way to get rid of circles)
map = folium.Map(location=[34,-118], 
                zoom_start=8, 
                control_scale=True,
                height=400,
                tiles='CartoDB dark_matter',
                attr= '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors &copy; <a href="https://carto.com/attributions">CARTO</a>')

# create a function to create circles, and also add a chart in the popup window (a lot here, will break it up later)
def createCircle(lat,lon,size,place,label):
    bar = alt.Chart(latimes.query('place == @place')).mark_bar().encode(
    #     x='date',
        x=alt.X('date', axis=alt.Axis(labels=False)),
        y='confirmed_cases',
        color='confirmed_cases',
        tooltip = ['date','place','confirmed_cases']
    ).properties(width=400,height=200)

    vega = folium.features.VegaLite(
        bar,
        width=600,
        height=200,
    )

    circle = folium.Circle(
        radius=size,
        location=[lat,lon],
        tooltip = label,
        color='crimson',
        fill = True
    )

    popup = folium.Popup()
    vega.add_to(popup)
    popup.add_to(circle)
    
    circle.add_to(map)
    

In [27]:
# loop through the rows in Los Angeles, and create a circle based on confirmed cases
for index, row in latimes_today.iterrows():
    label = str(row['confirmed_cases']) + ' confirmed cases in ' + row['place']
    createCircle(row['y'],row['x'],row['confirmed_cases'],row['place'],label)

In [28]:
map